<a href="https://colab.research.google.com/github/1900690/yolov10/blob/main/traking-yolov10.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!nvidia-smi

/bin/bash: line 1: nvidia-smi: command not found


In [2]:
!pip install -q supervision
!pip install -q git+https://github.com/THU-MIG/yolov10.git
!pip install deep-sort-realtime

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.0/124.0 kB 1.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.3/21.3 MB 62.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 47.7 MB/s eta 0:00:00


In [3]:
!mkdir -p weights
!wget -P weights -q https://github.com/jameslahm/yolov10/releases/download/v1.0/yolov10n.pt
!wget -P weights -q https://github.com/jameslahm/yolov10/releases/download/v1.0/yolov10s.pt
!wget -P weights -q https://github.com/jameslahm/yolov10/releases/download/v1.0/yolov10m.pt
!wget -P weights -q https://github.com/jameslahm/yolov10/releases/download/v1.0/yolov10b.pt
!wget -P weights -q https://github.com/jameslahm/yolov10/releases/download/v1.0/yolov10x.pt
!wget -P weights -q https://github.com/jameslahm/yolov10/releases/download/v1.0/yolov10l.pt
!ls -lh weights

total 408M
-rw-r--r-- 1 root root  80M May 23 09:38 yolov10b.pt
-rw-r--r-- 1 root root 100M May 23 09:38 yolov10l.pt
-rw-r--r-- 1 root root  64M May 23 09:38 yolov10m.pt
-rw-r--r-- 1 root root  11M May 23 09:38 yolov10n.pt
-rw-r--r-- 1 root root  32M May 23 09:38 yolov10s.pt
-rw-r--r-- 1 root root 123M May 23 09:38 yolov10x.pt


In [1]:
from IPython.display import HTML
from base64 import b64encode
def play_video(filename):
  html = ''
  video = open(filename,'rb').read()
  src = 'data:video/mp4;base64,' + b64encode(video).decode()
  html += fr'<video width=900 controls autoplay loop><source src="%s" type="video/mp4"></video>' % src
  return HTML(html)

In [6]:
import cv2
import torch
import datetime
import numpy as np
from absl import app, flags
from absl.flags import FLAGS
#from ultralytics import YOLOv10
from deep_sort_realtime.deepsort_tracker import DeepSort

ModuleNotFoundError: No module named 'ultralytics'

# Using Bytetrack

In [7]:
!yolo tracker="bytetrack.yaml"\
      mode=track\
      model='/content/weights/yolov10s.pt'\
      conf=0.25\
      save_txt=True\
      show_conf=False\
      source="/content/test.mp4"

Ultralytics YOLOv8.1.34 🚀 Python-3.10.12 torch-2.3.0+cu121 CPU (Intel Xeon 2.20GHz)
YOLOv10s summary (fused): 293 layers, 8096880 parameters, 86880 gradients, 24.8 GFLOPs

video 1/1 (frame 1/302) /content/test.mp4: 384x640 9 0s, 411.4ms
video 1/1 (frame 2/302) /content/test.mp4: 384x640 9 0s, 377.5ms
video 1/1 (frame 3/302) /content/test.mp4: 384x640 9 0s, 375.5ms
video 1/1 (frame 4/302) /content/test.mp4: 384x640 9 0s, 359.8ms
video 1/1 (frame 5/302) /content/test.mp4: 384x640 9 0s, 592.8ms
video 1/1 (frame 6/302) /content/test.mp4: 384x640 9 0s, 1 1, 612.3ms
video 1/1 (frame 7/302) /content/test.mp4: 384x640 9 0s, 1 1, 891.2ms
video 1/1 (frame 8/302) /content/test.mp4: 384x640 9 0s, 1 1, 1 26, 1105.1ms
video 1/1 (frame 9/302) /content/test.mp4: 384x640 9 0s, 1 1, 1 26, 1133.8ms
video 1/1 (frame 10/302) /content/test.mp4: 384x640 9 0s, 1 1, 1 26, 580.3ms
video 1/1 (frame 11/302) /content/test.mp4: 384x640 9 0s, 1 1, 1 26, 383.7ms
video 1/1 (frame 12/302) /content/test.mp4: 384x640 8 0

In [3]:
#AVIからmp4に変換
import cv2
import os

#この中の動画が画像変換される
file_path='/content/AVI/'

#mp4フォルダを作成
if not os.path.exists('/content/mp4'):
    os.mkdir('/content/mp4')

def convert_avi_to_mp4(file_path):
    #VideoCaptureオブジェクトを取得
    cap = cv2.VideoCapture(file_path)

    #動画のプロパティを取得
    width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
    fps = cap.get(cv2.CAP_PROP_FPS)

    #書き出し設定
    fourcc = cv2.VideoWriter_fourcc('m','p','4','v')
    writer = cv2.VideoWriter("/content/mp4/"+os.path.splitext(os.path.basename(file_path))[0]+".mp4", fourcc, fps, (width, height))

    while True:
        ret, frame = cap.read()
        writer.write(frame)
        if not ret:
            break

    writer.release()
    cap.release()


load_name = os.listdir(file_path)

for file_name in load_name:
  convert_avi_to_mp4(file_path+file_name)

In [5]:
!ffmpeg -hide_banner -loglevel error -i /content/mp4/test.mp4 -vcodec libx264 /content/output_test.mp4 -y
play_video("/content/output_test.mp4")